# Running Multiple Kriging Tasks

This notebook demonstrates how to run multiple kriging compute tasks concurrently
using the `run_kriging_multiple` function. This is useful for:

- Scenario analysis with different parameters
- Sensitivity studies varying neighborhood settings
- Batch processing multiple attributes

All kriging results are stored as attributes in a single Block Model.

## Authentication

In [1]:
from evo.notebooks import ServiceManagerWidget

manager = await ServiceManagerWidget.with_auth_code(
    client_id="core-compute-tasks-notebooks",
    base_uri="https://qa-ims.bentley.com",
    discovery_url="https://int-discover.test.api.seequent.com",
    cache_location="notebook-data",
).login()

ServiceManagerWidget(children=(VBox(children=(HBox(children=(Image(value=b'\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR…

## Setup for Local Development

> **Note:** If the imports below fail, you may need to add the local source packages to your Python path. Run the cell below first.

In [2]:
# Setup for local development source - run this cell FIRST if you get import errors
# You may need to restart your kernel after running this cell for the first time
import sys

# Remove any cached evo.compute modules to force reimport from local source
mods_to_remove = [key for key in list(sys.modules.keys()) if key.startswith('evo.compute')]
for mod in mods_to_remove:
    del sys.modules[mod]

local_paths = [
    r"C:\Source\evo-python-sdk\packages\evo-compute\src",
    r"C:\Source\evo-python-sdk\packages\evo-blockmodels\src",
    r"C:\Source\evo-python-sdk\packages\evo-objects\src",
    r"C:\Source\evo-python-sdk\packages\evo-sdk-common\src",
]
for path in local_paths:
    if path not in sys.path:
        sys.path.insert(0, path)

print("Local source paths configured - restart kernel if you still see import errors")

Local source paths configured - restart kernel if you still see import errors


## Load Source PointSet and Variogram

Load the source pointset and variogram that will be used for all scenarios.

In [3]:
from evo.notebooks import display_object_links
from evo.objects.typed import PointSet

# Replace with your actual object references
environment = manager.get_environment()
prefix = (
    f"{environment.hub_url}/geoscience-object/orgs/{environment.org_id}/workspaces/{environment.workspace_id}/objects"
)

source_pointset_ref = f"{prefix}/9100d7dc-44e9-4e61-b427-159635dea22f?version=1766012988078917061"
variogram_ref = f"{prefix}/72cd9b83-90f4-4cb0-9691-95728e3f9cbb?version=1765856020219372248"

# Load the source pointset
source_pointset = await PointSet.from_reference(manager, source_pointset_ref)
display_object_links(source_pointset, label="Source PointSet")
print(f"Source: {source_pointset.name}")

Source: Ag_LMS1 - Ag_ppm Values


## Create Target Block Model

Create a single Block Model to hold all scenario results as attributes.
The Block Model Service manages concurrent attribute creation.

In [4]:
import uuid
from evo.objects.typed import BlockModel, RegularBlockModelData, Point3, Size3i, Size3d
from evo.blockmodels import Units

run_uuid = uuid.uuid4()

# Create a Block Model to hold all scenario results
# Adjust origin, n_blocks, and block_size to match your data domain
bm_data = RegularBlockModelData(
    name=f"Kriging Scenarios - {run_uuid}",
    description="Block model with kriging results for different max_samples scenarios",
    origin=Point3(x=10000, y=100000, z=200),
    n_blocks=Size3i(nx=40, ny=40, nz=40),
    block_size=Size3d(dx=25.0, dy=25.0, dz=10.0),
    crs="EPSG:32632",
    size_unit_id=Units.METRES,
)

block_model = await BlockModel.create_regular(manager, bm_data)

print(f"Created Block Model: {block_model.name}")
print(f"Block Model UUID: {block_model.block_model_uuid}")
print(f"Bounding Box: {block_model.bounding_box}")
display_object_links(block_model, label="Target Block Model")

Created Block Model: Kriging Scenarios - ba7dc447-ebee-428f-b1b8-b83219d31c7d
Block Model UUID: ab610772-82e8-4380-a453-05828ac98679
Bounding Box: BoundingBox(min_x=10000.0, min_y=100000.0, max_x=11000.0, max_y=101000.0, min_z=200.0, max_z=600.0)


## Define Kriging Scenarios

Create multiple parameter sets varying the `max_samples` parameter to study its effect.
All scenarios target the same Block Model, creating different attributes.

In [9]:
from evo.compute.tasks import (
    KrigingParameters,
    Source,
    Target,
    OrdinaryKriging,
    KrigingSearch,
    Ellipsoid,
    EllipsoidRanges,
    Rotation,
)

# Define different max_samples values to test
max_samples_values = [5, 10, 15, 20]

# Search ellipsoid configuration
search_ellipsoid = Ellipsoid(
    ellipsoid_ranges=EllipsoidRanges(major=200.0, semi_major=150.0, minor=100.0),
    rotation=Rotation(dip_azimuth=0.0, dip=0.0, pitch=0.0),
)

# Create parameter sets for each scenario, all targeting the same Block Model
parameter_sets = []
for max_samples in max_samples_values:
    params = KrigingParameters(
        source=source_pointset.locations.attributes["Ag_ppm Values"],
        target=Target.new_attribute(block_model, attribute_name=f"Samples={max_samples}"),
        kriging_method=OrdinaryKriging(),
        variogram=variogram_ref,
        neighborhood=KrigingSearch(ellipsoid=search_ellipsoid, max_samples=max_samples),
    )
    parameter_sets.append(params)
    print(f"Prepared scenario with max_samples={max_samples}")

print(f"\nCreated {len(parameter_sets)} parameter sets")

Prepared scenario with max_samples=5
Prepared scenario with max_samples=10
Prepared scenario with max_samples=15
Prepared scenario with max_samples=20

Created 4 parameter sets


## Run Multiple Kriging Tasks

Execute all scenarios concurrently using `run_kriging_multiple`.
Progress is aggregated across all tasks.

In [10]:
from evo.compute.tasks import run_kriging_multiple
from evo.notebooks import FeedbackWidget

# Run all scenarios in parallel
print(f"Submitting {len(parameter_sets)} kriging tasks in parallel...")
fb = FeedbackWidget("Kriging Scenarios")

results = await run_kriging_multiple(manager, parameter_sets, fb=fb)

print(f"\nAll {len(results)} scenarios completed!")

Submitting 4 kriging tasks in parallel...



All 4 scenarios completed!


## Query Results from Block Model

Get all scenario results from the Block Model.

In [11]:
# Query the Block Model for all scenario columns
scenario_columns = [f"Samples={ms}" for ms in max_samples_values]

print("Querying Block Model for results...")
df = await block_model.get_data(columns=scenario_columns)

print(f"Retrieved {len(df)} blocks with {len(scenario_columns)} scenario columns")
df.head(10)

Querying Block Model for results...
Retrieved 64000 blocks with 4 scenario columns


x         y      z  Samples=5  Samples=10  Samples=15  Samples=20
0  10662.5  100012.5  405.0        NaN         NaN         NaN         NaN
1  10662.5  100012.5  415.0        NaN         NaN         NaN         NaN
2  10662.5  100012.5  425.0        NaN         NaN         NaN         NaN
3  10662.5  100012.5  435.0        NaN         NaN         NaN         NaN
4  10662.5  100012.5  445.0        NaN         NaN         NaN         NaN
5  10662.5  100012.5  455.0        NaN         NaN         NaN         NaN
6  10662.5  100012.5  465.0        NaN         NaN         NaN         NaN
7  10662.5  100012.5  475.0        NaN         NaN         NaN         NaN
8  10662.5  100012.5  485.0        NaN         NaN         NaN         NaN
9  10662.5  100012.5  495.0        NaN         NaN         NaN         NaN

## Display Results

In [12]:
# Display link to the Block Model with all scenarios
display_object_links(block_model, label="Block Model with all scenarios")

# Show individual result messages
for i, (result, max_samples) in enumerate(zip(results, max_samples_values)):
    print(f"Scenario {i+1}: max_samples={max_samples} - {result.message}")

Scenario 1: max_samples=5 - Kriging completed.
Scenario 2: max_samples=10 - Kriging completed.
Scenario 3: max_samples=15 - Kriging completed.
Scenario 4: max_samples=20 - Kriging completed.


## Analyze Results

Compare the kriging results across different max_samples values.

In [13]:
# Show statistics for each scenario
print("Statistics by max_samples:")
print(df[scenario_columns].describe())

Statistics by max_samples:
          Samples=5    Samples=10    Samples=15    Samples=20
count  10649.000000  10649.000000  10649.000000  10649.000000
mean     112.093617    111.122638    111.041452    110.780011
std       70.023416     64.705758     61.856261     59.592869
min        6.887604      8.570578     11.116600     11.116600
25%       57.448091     62.219550     64.765351     67.859388
50%      102.442995    103.043904    102.803484    102.203295
75%      141.242807    137.407133    136.124138    136.126375
max      677.854549    685.066753    538.751039    479.741686


In [14]:
# Optional: Visualize the differences using plotly
try:
    import plotly.express as px

    # Melt the data for box plot comparison
    df_melted = df[scenario_columns].melt(var_name="Scenario", value_name="value")

    fig = px.box(
        df_melted,
        x="Scenario",
        y="value",
        title="Kriging Values by Max Samples",
    )
    fig.show()
except ImportError:
    print("Install plotly for visualization: pip install plotly")
